## The Mapping of the German Windcrafts Numbers per Landkreis

In [47]:
import geopandas as gpd
import pandas as pd
from shapely import wkt
import folium
from folium.features import GeoJsonTooltip
from folium.plugins import FloatImage
import base64
import requests
from zipfile import ZipFile
from io import BytesIO

In [48]:
#Loading of two datasets
#The windparks
df=pd.read_csv('Landkreis_id-windanlage.csv')

# URL to the NUTS 2021 GIS data in Shapefile format provided by Eurostat
url = "https://gisco-services.ec.europa.eu/distribution/v2/nuts/download/ref-nuts-2021-01m.shp.zip"

# Send a request to the URL to download the zip file
response = requests.get(url)
zip_file = ZipFile(BytesIO(response.content))

# Extract the shapefile corresponding to NUTS level 3 (you may need to adjust the filename based on the contents)
zip_file.extractall("Users/solozobovavaleria/Downloads/ref_nuts_2021_01m")

# Load the shapefile using Geopandas
kshape = gpd.read_file("Users/solozobovavaleria/Downloads/ref_nuts_2021_01m/NUTS_RG_01M_2021_4326_LEVL_3.shp.zip")

# Filter for Germany's NUTS3 regions
kshape = kshape[(kshape["LEVL_CODE"] == 3) & (kshape["CNTR_CODE"] == "DE")]

In [49]:
kshape.shape

(401, 10)

In [50]:
df.rename(columns={'Code':'NUTS_ID'}, inplace=True)
df.shape

(4693, 15)

In [51]:
#Create additional variable 
df['Age']=2024-df['Baujahr']
df.head(3)

Unnamed: 0  Baujahr  Gesamt- leistung (MW)  Anzahl         Typ (WKA)  \
0           0     2017                    2.0       1    Qreon Q82 (1×)   
1           1     2017                    2.0       1    Qreon Q82 (1×)   
2           2     2003                    1.5       1  Südwind S70 (1×)   

                       Ort Land- kreis  \
0                Karlsruhe          KA   
1                Karlsruhe          KA   
2  Bad Peterstal-Griesbach          OG   

                      Projektierer / Betreiber  \
0                               Fraunhofer ICT   
1                               Fraunhofer ICT   
2  Schmalz, Windenergieanlage „Bei der Schanz“   

                                         Bemerkungen      Latitude  \
0  Forschungsprojekt mit kombiniertem Batteriespe...    49° 1′ 9″    
1  Forschungsprojekt mit kombiniertem Batteriespe...    49° 1′ 9″    
2  errichtet an der Schwarzwaldhochstraße im Bere...  48° 28′ 22″    

     Longitude NUTS_ID           NUTS 1.1   NUTS 2.1                   Name  \
0   8° 31′ 4″    DE123  Baden-Württemberg  Karlsruhe   Karlsruhe, Landkreis   
1   8° 31′ 4″    DE122  Baden-Württemberg  Karlsruhe  Karlsruhe, Stadtkreis   
2   8° 16′ 7″    DE134  Baden-Württemberg   Freiburg           Ortenaukreis   

   Age  
0    7  
1    7  
2   21

In [52]:

df=df.groupby(['NUTS_ID']).agg({'Anzahl':'sum', 'Gesamt- leistung (MW)':'sum', 'Age':'mean'}).sort_values(by='Anzahl',ascending=False)
df.head(10)

Anzahl  Gesamt- leistung (MW)   Age
NUTS_ID                                     
DEF05       854               2312.723  14.0
DEF07       854               2480.540  14.0
DE40I       667               1666.850  14.0
DE40F       577               1240.700  14.0
DEA47       544               1358.505  14.0
DEF0C       521               1448.220  14.0
DE932       516                802.075  14.0
DE949       499               1253.450  14.0
DE947       487                868.455  14.0
DEE07       440                775.850  14.0

In [53]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 343 entries, DEF05 to DE111
Data columns (total 3 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Anzahl                 343 non-null    int64  
 1   Gesamt- leistung (MW)  343 non-null    float64
 2   Age                    343 non-null    float64
dtypes: float64(2), int64(1)
memory usage: 10.7+ KB


In [54]:
kshape.head(3)

NUTS_ID  LEVL_CODE CNTR_CODE            NAME_LATN            NUTS_NAME  \
1   DE933          3        DE              Harburg              Harburg   
2   DE934          3        DE    Lüchow-Dannenberg    Lüchow-Dannenberg   
6   DE935          3        DE  Lüneburg, Landkreis  Lüneburg, Landkreis   

   MOUNT_TYPE  URBN_TYPE  COAST_TYPE    FID  \
1           4          2           3  DE933   
2           4          3           3  DE934   
6           4          2           3  DE935   

                                            geometry  
1  MULTIPOLYGON (((10.30795 53.43320, 10.33096 53...  
2  POLYGON ((11.17186 53.15664, 11.17785 53.15046...  
6  MULTIPOLYGON (((10.59505 53.36393, 10.61666 53...

In [55]:
new_data=pd.merge(kshape, df, how ='left', on='NUTS_ID')
new_data.head(3)

NUTS_ID  LEVL_CODE CNTR_CODE            NAME_LATN            NUTS_NAME  \
0   DE933          3        DE              Harburg              Harburg   
1   DE934          3        DE    Lüchow-Dannenberg    Lüchow-Dannenberg   
2   DE935          3        DE  Lüneburg, Landkreis  Lüneburg, Landkreis   

   MOUNT_TYPE  URBN_TYPE  COAST_TYPE    FID  \
0           4          2           3  DE933   
1           4          3           3  DE934   
2           4          2           3  DE935   

                                            geometry  Anzahl  \
0  MULTIPOLYGON (((10.30795 53.43320, 10.33096 53...    84.0   
1  POLYGON ((11.17186 53.15664, 11.17785 53.15046...    77.0   
2  MULTIPOLYGON (((10.59505 53.36393, 10.61666 53...   114.0   

   Gesamt- leistung (MW)   Age  
0                 212.27  14.0  
1                 143.00  14.0  
2                 265.25  14.0

In [56]:
new_data.info()
#Merge of dataframes produces NaN (because in some Kreis there are no inforamtion about windparks)
#I replace the nan in Anzahl, Age, Gesamt- leistung (MW) 
new_data['Anzahl'].fillna(0, inplace=True)
new_data['Age'].fillna(0, inplace=True)
new_data['Gesamt- leistung (MW)'].fillna(0, inplace=True)
#the results are:
new_data.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 401 entries, 0 to 400
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype   
---  ------                 --------------  -----   
 0   NUTS_ID                401 non-null    object  
 1   LEVL_CODE              401 non-null    int64   
 2   CNTR_CODE              401 non-null    object  
 3   NAME_LATN              401 non-null    object  
 4   NUTS_NAME              401 non-null    object  
 5   MOUNT_TYPE             401 non-null    int64   
 6   URBN_TYPE              401 non-null    int64   
 7   COAST_TYPE             401 non-null    int64   
 8   FID                    401 non-null    object  
 9   geometry               401 non-null    geometry
 10  Anzahl                 343 non-null    float64 
 11  Gesamt- leistung (MW)  343 non-null    float64 
 12  Age                    343 non-null    float64 
dtypes: float64(3), geometry(1), int64(4), object(5)
memory usage: 40.9+ KB
<class 'geopanda

In [100]:
mymap = folium.Map()

In [101]:
# Initialize the map object
# Compute centroids of the map
new_data = gpd.GeoDataFrame(new_data)
x_map = new_data.centroid.x.mean()
y_map = new_data.centroid.y.mean()

mymap = folium.Map(location=[y_map, x_map], zoom_start=6.3, tiles=None)
folium.TileLayer('CartoDB positron', control=False).add_to(mymap)

/var/folders/bg/6h6fxpzx7_v6jgvd0c31r_7m0000gn/T/ipykernel_21088/3302045972.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  x_map = new_data.centroid.x.mean()
/var/folders/bg/6h6fxpzx7_v6jgvd0c31r_7m0000gn/T/ipykernel_21088/3302045972.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  y_map = new_data.centroid.y.mean()


In [102]:
# Import folium DivIcon plugin
from folium.features import DivIcon
cities=('Karlsruhe ', 'Berlin', 'Deutschland', 'NordSee Offshore Wind-Parks', 'OstSee Offshore-WindParks')
coordinates=([49.0, 8.4], [52.52, 13.41], [53.0, 5.8], [55, 5.7], [55,  13.4] )



folium.Circle(coordinates[0], radius=200, color='#3186cc', fill=True).add_child(folium.Popup(cities[0])).add_to(mymap)
folium.map.Marker(coordinates[0], icon=DivIcon(icon_size=(20,20),icon_anchor=(0,0), html='<div style="font-size: 12; color:#d3186cc;"><b>%s</b></div>' % cities[0], )).add_to(mymap)
folium.Circle(coordinates[1], radius=200, color='#3186cc', fill=True).add_child(folium.Popup(cities[1])).add_to(mymap)
folium.map.Marker(coordinates[1], icon=DivIcon(icon_size=(20,20),icon_anchor=(0,0), html='<div style="font-size: 12; color:#d3186cc;"><b>%s</b></div>' % cities[1], )).add_to(mymap)

#folium.Circle(coordinates[2], radius=400, color='#3186cc', fill=True).add_child(folium.Popup(cities[2])).add_to(mymap)
#folium.map.Marker(coordinates[2], icon=DivIcon(icon_size=(30,30),icon_anchor=(0,0), html='<div style="font-size: 40; color:#d3186cc;"><b>%s</b></div>' % cities[2], )).add_to(mymap)
folium.Circle(coordinates[3], radius=200, color='#3186cc', fill=True).add_child(folium.Popup(cities[3])).add_to(mymap)
folium.map.Marker(coordinates[3], icon=DivIcon(icon_size=(20,20),icon_anchor=(0,0), html='<div style="font-size: 12; color:#d3186cc;"><b>%s</b></div>' % cities[3], )).add_to(mymap)

folium.Circle(coordinates[4], radius=200, color='#3186cc', fill=True).add_child(folium.Popup(cities[4])).add_to(mymap)
folium.map.Marker(coordinates[4], icon=DivIcon(icon_size=(20,20),icon_anchor=(0,0), html='<div style="font-size: 12; color:#d3186cc;"><b>%s</b></div>' % cities[4], )).add_to(mymap)


circle = folium.Circle(coordinates[2], radius=1000, color='#d35400', fill=True).add_child(folium.Popup('Deutschland'))

marker = folium.map.Marker(
    coordinates[2],
    # Create an icon as a text label
    icon=DivIcon(
        icon_size=(50,50),
        icon_anchor=(0,0),
        html='<div style="font-size: 40; color:#d35400;"><b>%s</b></div>' % 'Deutschland',
        )
    )
mymap.add_child(circle)
mymap.add_child(marker)




mymap
 


In [103]:
loc = 'Deutschland'
title_html = f'<h1 style="position:absolute;z-index:100000;left:40vw" >{loc}</h1>'   



mymap.get_root().html.add_child(folium.Element(title_html))

mymap


### Label the offshores windparks of germany:

In [104]:
#I have to load the dataframe

offshores_final=pd.read_csv('Offshores_Windparks.csv')
offshores_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 33 entries, 0 to 32
Data columns (total 6 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Unnamed: 0     33 non-null     int64  
 1   Name           33 non-null     object 
 2   Anzahl WKAs    33 non-null     int64  
 3   Latitude_cor   33 non-null     float64
 4   Longitude_cor  33 non-null     float64
 5   Status         33 non-null     object 
dtypes: float64(2), int64(2), object(2)
memory usage: 1.7+ KB


In [105]:
offshores_final.head(3)

Unnamed: 0             Name  Anzahl WKAs  Latitude_cor  Longitude_cor  \
0           1     alpha ventus           12     54.008333       6.598333   
1           2  BARD Offshore I           80     54.358333       5.975000   
2           3          Riffgat           30     53.690000       6.480000   

       Status  
0  in Betrieb  
1  in Betrieb  
2  in Betrieb

In [106]:

# Import folium MarkerCluster plugin
from folium.plugins import MarkerCluster
marker_cluster = MarkerCluster()
# Add marker_cluster to current site_map




In [107]:
mymap.add_child(marker_cluster)


for index, record in offshores_final.iterrows():
    coordinate = [record['Latitude_cor'], record['Longitude_cor']]
    
    marker=folium.map.Marker(coordinate, popup=record['Name'], icon=folium.Icon(color='red')).add_to(marker_cluster)
    marker_cluster.add_child(marker)

mymap




In [108]:
# Define the tooltips
tooltip_number = GeoJsonTooltip(
    fields=['NUTS_NAME', 'Anzahl'],
    aliases=['Landkreis: ', 'Anzahl: '],
    localize=True,
    sticky=False,
    smooth_factor=0,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
        font-size: 12px;
    """,
    max_width=750,
)

tooltip_age = GeoJsonTooltip(
    fields=['NUTS_NAME', 'Age'],
    aliases=['Landkreris:', 'The Average age: '],
    localize=True,
    sticky=False,
    smooth_factor=0,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
        font-size: 12px;
    """,
    max_width=750
)

In [109]:
# Create and add choropleth layers
choropleth_wind_crafts = folium.Choropleth(
    geo_data=new_data, name='Number of windcrafts', data=new_data,
    columns=['NUTS_ID', 'Anzahl'], key_on='feature.properties.NUTS_ID',
    fill_color='Greens', bins=10, fill_opacity=1, line_opacity=0.2,
    smooth_factor=0, use_jenks=True, overlay=False
).add_to(mymap)
choropleth_wind_crafts.geojson.add_child(tooltip_number)

choropleth_age = folium.Choropleth(
    geo_data=new_data, name='The average age of windcrafts', data=new_data,
    columns=['NUTS_ID', 'Age'], key_on='feature.properties.NUTS_ID',
    fill_color='Blues', bins=10, fill_opacity=0.6, line_opacity=0.2,
    smooth_factor=0, use_jenks=True, overlay=False, show=False
).add_to(mymap)
choropleth_age.geojson.add_child(tooltip_age)

In [110]:
# Add LayerControl
folium.LayerControl(collapsed=False).add_to(mymap)
mymap

In [111]:
# Save map
mymap.save('Users/solozobovavaleria/German_windparks.html')